In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib as plt
from scipy import stats
from tqdm import tqdm

In [2]:
inputFile = "MAESTRO-d6178bdd-identified_variants_merged_protein_regions-main.tsv"
data = pd.read_csv(inputFile,sep='\t',low_memory=False)

In [3]:
data_processed = data[['Peptide'] + [c for c in data.columns if 'intensity_for_peptide_variant' in c]]

In [4]:
data_processed.replace(0.0,np.nan, inplace = True)

/tmp/ipykernel_620/24937952.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data_processed.replace(0.0,np.nan, inplace = True)


In [5]:
data_processed = data_processed.set_index("Peptide")

In [6]:
data_processed = data_processed.T

In [7]:
data_processed.index = data_processed.index.map(lambda x:'.'.join(x.split('.')[:2]))

In [8]:
def create_label(x):
    if "#Healthy" in x:
        return 1
    elif "#Non-severe-COVID-19" in x:
        return 2
    elif "#Severe-COVID-19" in x:
        return 3
    elif "#Symptomatic-non-COVID-19" in x:
        return 4
    else:
        return 0
data_processed["label"]=data_processed.index.map(lambda x: create_label(x))

In [9]:
data_processed = data_processed[data_processed['label']!=0]

In [10]:
#Filter Data based on NaN for each label
per_label_count = data_processed.groupby('label').count()
filterCondition = (per_label_count >= 18).all()
filter_per_label = per_label_count.loc[:, filterCondition]
filter_column = list(filter_per_label.columns) +['label']
filter_data =  data_processed[filter_column]

In [11]:
for column in tqdm(filter_data):
    if column != "label":
        filter_data[column] = filter_data.groupby("label")[column].transform(lambda x: x.fillna(x.mean()))

  0%|          | 0/90 [00:00<?, ?it/s]/tmp/ipykernel_620/3972711595.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filter_data[column] = filter_data.groupby("label")[column].transform(lambda x: x.fillna(x.mean()))
/tmp/ipykernel_620/3972711595.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filter_data[column] = filter_data.groupby("label")[column].transform(lambda x: x.fillna(x.mean()))
/tmp/ipykernel_620/3972711595.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice fr

In [12]:
##filter_data.to_csv("filterd_data.tsv", sep="\t")

In [13]:
filter_data

Peptide                                            R.[304.207]QQQHLFGSNVTD(C,57.021)SGNF(C,57.021)LFR.S  \
_dyn_#Healthy.HC1                                                                           0.101284      
_dyn_#Healthy.HC10                                                                          0.211214      
_dyn_#Healthy.HC12                                                                          0.094757      
_dyn_#Healthy.HC13                                                                          0.128179      
_dyn_#Healthy.HC17                                                                          0.104670      
...                                                                                              ...      
_dyn_#Symptomatic-non-COVID-19.JBDZ6                                                        0.031197      
_dyn_#Symptomatic-non-COVID-19.JBDZ7                                                        0.063094      
_dyn_#Symptomatic-non-COVID-19.JBDZ8                                                        0.067680      
_dyn_#Symptomatic-non-COVID-19.JBDZ9                                                        0.095905      
_dyn_#Symptomatic-non-COVID-19.Patient-group-jbdz                                           0.011803      

Peptide                                            R.[304.207]QQQHLF(G,304.219)SNVTD(C,57.021)SGNF(C,57.021)LFR.S  \
_dyn_#Healthy.HC1                                                                           1.352256                
_dyn_#Healthy.HC10                                                                          0.366582                
_dyn_#Healthy.HC12                                                                          0.174988                
_dyn_#Healthy.HC13                                                                          0.282839                
_dyn_#Healthy.HC17                                                                          0.312750                
...                                                                                              ...                
_dyn_#Symptomatic-non-COVID-19.JBDZ6                                                        0.218505                
_dyn_#Symptomatic-non-COVID-19.JBDZ7                                                        0.168100                
_dyn_#Symptomatic-non-COVID-19.JBDZ8                                                        0.249860                
_dyn_#Symptomatic-non-COVID-19.JBDZ9                                                        0.319936                
_dyn_#Symptomatic-non-COVID-19.Patient-group-jbdz                                           0.314668                

Peptide                                            K.[304.207]DLLFRDDTV(C,57.021)(L,134.957)A(K,304.207).L  \
_dyn_#Healthy.HC1                                                                           0.272530         
_dyn_#Healthy.HC10                                                                          0.296847         
_dyn_#Healthy.HC12                                                                          0.147994         
_dyn_#Healthy.HC13                                                                          0.277178         
_dyn_#Healthy.HC17                                                                          0.932067         
...                                                                                              ...         
_dyn_#Symptomatic-non-COVID-19.JBDZ6                                                        0.113378         
_dyn_#Symptomatic-non-COVID-19.JBDZ7                                                        0.156081         
_dyn_#Symptomatic-non-COVID-19.JBDZ8                                                        0.257619         
_dyn_#Symptomatic-non-COVID-19.JBDZ9                                                        0.271392         
_dyn_#Symptomatic-non-COVID-19.Patient-group-jbdz                                           0.523605

In [14]:
# corr1 = filter_data.corr()

In [15]:
# cor_matrix = corr1.abs()

In [16]:
# upper_tri = cor_matrix.where(np.triu(np.ones(cor_matrix.shape),k=1).astype(np.bool))

In [17]:
# to_drop = [column for column in upper_tri.columns if any(upper_tri[column] > 0.95)]

In [18]:
# data_processed_1 = filter_data.drop(filter_data.columns[to_drop], axis=1)

In [19]:
data_correlated = filter_data.corr()

In [20]:
data_correlated

Peptide                                             R.[304.207]QQQHLFGSNVTD(C,57.021)SGNF(C,57.021)LFR.S  \
Peptide                                                                                                    
R.[304.207]QQQHLFGSNVTD(C,57.021)SGNF(C,57.021)...                                           1.000000      
R.[304.207]QQQHLF(G,304.219)SNVTD(C,57.021)SGNF...                                          -0.147077      
K.[304.207]DLLFRDDTV(C,57.021)(L,134.957)A(K,30...                                           0.210361      
R.[304.207]DDTV(C,58.003)LA(K,304.207).L                                                     0.757234      
K.[304.207]DLLF(R,-18.004)DDTV(C,57.021)LA(K,30...                                           0.314623      
...                                                                                               ...      
K.[304.207]YLGEE(Y,21.985)V(K,304.207).A                                                    -0.465838      
K.[304.207]YL(G,13.987)EEYV(K,304.207).A                                                     0.458353      
K.[304.207]YLGEEY(V,-18.002)(K,304.207).A                                                   -0.049074      
K.[304.207]YLGEE(Y,-20.114)V(K,304.207).A                                                   -0.013072      
label                                                                                       -0.028810      

Peptide                                             R.[304.207]QQQHLF(G,304.219)SNVTD(C,57.021)SGNF(C,57.021)LFR.S  \
Peptide                                                                                                              
R.[304.207]QQQHLFGSNVTD(C,57.021)SGNF(C,57.021)...                                          -0.147077                
R.[304.207]QQQHLF(G,304.219)SNVTD(C,57.021)SGNF...                                           1.000000                
K.[304.207]DLLFRDDTV(C,57.021)(L,134.957)A(K,30...                                          -0.081191                
R.[304.207]DDTV(C,58.003)LA(K,304.207).L                                                    -0.301039                
K.[304.207]DLLF(R,-18.004)DDTV(C,57.021)LA(K,30...                                           0.224343                
...                                                                                               ...                
K.[304.207]YLGEE(Y,21.985)V(K,304.207).A                                                     0.363800                
K.[304.207]YL(G,13.987)EEYV(K,304.207).A                                                    -0.005968                
K.[304.207]YLGEEY(V,-18.002)(K,304.207).A                                                    0.194494                
K.[304.207]YLGEE(Y,-20.114)V(K,304.207).A                                                    0.257172                
label                                                                                       -0.136155                

Peptide                                             K.[304.207]DLLFRDDTV(C,57.021)(L,134.957)A(K,304.207).L  \
Peptide                                                                                                       
R.[304.207]QQQHLFGSNVTD(C,57.021)SGNF(C,57.021)...                                           0.210361         
R.[304.207]QQQHLF(G,304.219)SNVTD(C,57.021)SGNF...                                          -0.081191         
K.[304.207]DLLFRDDTV(C,57.021)(L,134.957)A(K,30...                                           1.000000         
R.[304.207]DDTV(C,58.003)LA(K,304.207).L                                                     0.270530         
K.[304.207]DLLF(R,-18.004)DDTV(C,57.021)LA(K,30...                                           0.516228         
...                                                                                               ...         
K.[304.207]YLGEE(Y,21.985)V(K,304.207).A                                                     0.504976         
K.[304.207]YL(G,13.987)EEYV(K,304.207).A                     

In [21]:
corr_matrix = data_correlated.abs()

In [22]:
corr_matrix

Peptide                                             R.[304.207]QQQHLFGSNVTD(C,57.021)SGNF(C,57.021)LFR.S  \
Peptide                                                                                                    
R.[304.207]QQQHLFGSNVTD(C,57.021)SGNF(C,57.021)...                                           1.000000      
R.[304.207]QQQHLF(G,304.219)SNVTD(C,57.021)SGNF...                                           0.147077      
K.[304.207]DLLFRDDTV(C,57.021)(L,134.957)A(K,30...                                           0.210361      
R.[304.207]DDTV(C,58.003)LA(K,304.207).L                                                     0.757234      
K.[304.207]DLLF(R,-18.004)DDTV(C,57.021)LA(K,30...                                           0.314623      
...                                                                                               ...      
K.[304.207]YLGEE(Y,21.985)V(K,304.207).A                                                     0.465838      
K.[304.207]YL(G,13.987)EEYV(K,304.207).A                                                     0.458353      
K.[304.207]YLGEEY(V,-18.002)(K,304.207).A                                                    0.049074      
K.[304.207]YLGEE(Y,-20.114)V(K,304.207).A                                                    0.013072      
label                                                                                        0.028810      

Peptide                                             R.[304.207]QQQHLF(G,304.219)SNVTD(C,57.021)SGNF(C,57.021)LFR.S  \
Peptide                                                                                                              
R.[304.207]QQQHLFGSNVTD(C,57.021)SGNF(C,57.021)...                                           0.147077                
R.[304.207]QQQHLF(G,304.219)SNVTD(C,57.021)SGNF...                                           1.000000                
K.[304.207]DLLFRDDTV(C,57.021)(L,134.957)A(K,30...                                           0.081191                
R.[304.207]DDTV(C,58.003)LA(K,304.207).L                                                     0.301039                
K.[304.207]DLLF(R,-18.004)DDTV(C,57.021)LA(K,30...                                           0.224343                
...                                                                                               ...                
K.[304.207]YLGEE(Y,21.985)V(K,304.207).A                                                     0.363800                
K.[304.207]YL(G,13.987)EEYV(K,304.207).A                                                     0.005968                
K.[304.207]YLGEEY(V,-18.002)(K,304.207).A                                                    0.194494                
K.[304.207]YLGEE(Y,-20.114)V(K,304.207).A                                                    0.257172                
label                                                                                        0.136155                

Peptide                                             K.[304.207]DLLFRDDTV(C,57.021)(L,134.957)A(K,304.207).L  \
Peptide                                                                                                       
R.[304.207]QQQHLFGSNVTD(C,57.021)SGNF(C,57.021)...                                           0.210361         
R.[304.207]QQQHLF(G,304.219)SNVTD(C,57.021)SGNF...                                           0.081191         
K.[304.207]DLLFRDDTV(C,57.021)(L,134.957)A(K,30...                                           1.000000         
R.[304.207]DDTV(C,58.003)LA(K,304.207).L                                                     0.270530         
K.[304.207]DLLF(R,-18.004)DDTV(C,57.021)LA(K,30...                                           0.516228         
...                                                                                               ...         
K.[304.207]YLGEE(Y,21.985)V(K,304.207).A                                                     0.504976         
K.[304.207]YL(G,13.987)EEYV(K,304.207).A                     

In [25]:
upper_tri = corr_matrix.where(np.triu(np.ones(corr_matrix.shape),k=1).astype(np.bool))

/tmp/ipykernel_620/1559577561.py:1: DeprecationWarning: `np.bool` is a deprecated alias for the builtin `bool`. To silence this warning, use `bool` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.bool_` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  upper_tri = corr_matrix.where(np.triu(np.ones(corr_matrix.shape),k=1).astype(np.bool))


In [26]:
upper_tri

Peptide                                             R.[304.207]QQQHLFGSNVTD(C,57.021)SGNF(C,57.021)LFR.S  \
Peptide                                                                                                    
R.[304.207]QQQHLFGSNVTD(C,57.021)SGNF(C,57.021)...                                                NaN      
R.[304.207]QQQHLF(G,304.219)SNVTD(C,57.021)SGNF...                                                NaN      
K.[304.207]DLLFRDDTV(C,57.021)(L,134.957)A(K,30...                                                NaN      
R.[304.207]DDTV(C,58.003)LA(K,304.207).L                                                          NaN      
K.[304.207]DLLF(R,-18.004)DDTV(C,57.021)LA(K,30...                                                NaN      
...                                                                                               ...      
K.[304.207]YLGEE(Y,21.985)V(K,304.207).A                                                          NaN      
K.[304.207]YL(G,13.987)EEYV(K,304.207).A                                                          NaN      
K.[304.207]YLGEEY(V,-18.002)(K,304.207).A                                                         NaN      
K.[304.207]YLGEE(Y,-20.114)V(K,304.207).A                                                         NaN      
label                                                                                             NaN      

Peptide                                             R.[304.207]QQQHLF(G,304.219)SNVTD(C,57.021)SGNF(C,57.021)LFR.S  \
Peptide                                                                                                              
R.[304.207]QQQHLFGSNVTD(C,57.021)SGNF(C,57.021)...                                           0.147077                
R.[304.207]QQQHLF(G,304.219)SNVTD(C,57.021)SGNF...                                                NaN                
K.[304.207]DLLFRDDTV(C,57.021)(L,134.957)A(K,30...                                                NaN                
R.[304.207]DDTV(C,58.003)LA(K,304.207).L                                                          NaN                
K.[304.207]DLLF(R,-18.004)DDTV(C,57.021)LA(K,30...                                                NaN                
...                                                                                               ...                
K.[304.207]YLGEE(Y,21.985)V(K,304.207).A                                                          NaN                
K.[304.207]YL(G,13.987)EEYV(K,304.207).A                                                          NaN                
K.[304.207]YLGEEY(V,-18.002)(K,304.207).A                                                         NaN                
K.[304.207]YLGEE(Y,-20.114)V(K,304.207).A                                                         NaN                
label                                                                                             NaN                

Peptide                                             K.[304.207]DLLFRDDTV(C,57.021)(L,134.957)A(K,304.207).L  \
Peptide                                                                                                       
R.[304.207]QQQHLFGSNVTD(C,57.021)SGNF(C,57.021)...                                           0.210361         
R.[304.207]QQQHLF(G,304.219)SNVTD(C,57.021)SGNF...                                           0.081191         
K.[304.207]DLLFRDDTV(C,57.021)(L,134.957)A(K,30...                                                NaN         
R.[304.207]DDTV(C,58.003)LA(K,304.207).L                                                          NaN         
K.[304.207]DLLF(R,-18.004)DDTV(C,57.021)LA(K,30...                                                NaN         
...                                                                                               ...         
K.[304.207]YLGEE(Y,21.985)V(K,304.207).A                                                          NaN         
K.[304.207]YL(G,13.987)EEYV(K,304.207).A                     

In [27]:
to_drop = [column for column in upper_tri.columns if any(upper_tri[column] > 0.90)]

In [28]:
# to_drop
len(to_drop)

5594

In [29]:
filter_data = filter_data.drop(columns=to_drop)

In [31]:
filter_data

Peptide                                            R.[304.207]QQQHLFGSNVTD(C,57.021)SGNF(C,57.021)LFR.S  \
_dyn_#Healthy.HC1                                                                           0.101284      
_dyn_#Healthy.HC10                                                                          0.211214      
_dyn_#Healthy.HC12                                                                          0.094757      
_dyn_#Healthy.HC13                                                                          0.128179      
_dyn_#Healthy.HC17                                                                          0.104670      
...                                                                                              ...      
_dyn_#Symptomatic-non-COVID-19.JBDZ6                                                        0.031197      
_dyn_#Symptomatic-non-COVID-19.JBDZ7                                                        0.063094      
_dyn_#Symptomatic-non-COVID-19.JBDZ8                                                        0.067680      
_dyn_#Symptomatic-non-COVID-19.JBDZ9                                                        0.095905      
_dyn_#Symptomatic-non-COVID-19.Patient-group-jbdz                                           0.011803      

Peptide                                            R.[304.207]QQQHLF(G,304.219)SNVTD(C,57.021)SGNF(C,57.021)LFR.S  \
_dyn_#Healthy.HC1                                                                           1.352256                
_dyn_#Healthy.HC10                                                                          0.366582                
_dyn_#Healthy.HC12                                                                          0.174988                
_dyn_#Healthy.HC13                                                                          0.282839                
_dyn_#Healthy.HC17                                                                          0.312750                
...                                                                                              ...                
_dyn_#Symptomatic-non-COVID-19.JBDZ6                                                        0.218505                
_dyn_#Symptomatic-non-COVID-19.JBDZ7                                                        0.168100                
_dyn_#Symptomatic-non-COVID-19.JBDZ8                                                        0.249860                
_dyn_#Symptomatic-non-COVID-19.JBDZ9                                                        0.319936                
_dyn_#Symptomatic-non-COVID-19.Patient-group-jbdz                                           0.314668                

Peptide                                            K.[304.207]DLLFRDDTV(C,57.021)(L,134.957)A(K,304.207).L  \
_dyn_#Healthy.HC1                                                                           0.272530         
_dyn_#Healthy.HC10                                                                          0.296847         
_dyn_#Healthy.HC12                                                                          0.147994         
_dyn_#Healthy.HC13                                                                          0.277178         
_dyn_#Healthy.HC17                                                                          0.932067         
...                                                                                              ...         
_dyn_#Symptomatic-non-COVID-19.JBDZ6                                                        0.113378         
_dyn_#Symptomatic-non-COVID-19.JBDZ7                                                        0.156081         
_dyn_#Symptomatic-non-COVID-19.JBDZ8                                                        0.257619         
_dyn_#Symptomatic-non-COVID-19.JBDZ9                                                        0.271392         
_dyn_#Symptomatic-non-COVID-19.Patient-group-jbdz                                           0.523605

In [32]:
filter_data = filter_data.sample(frac=1)

In [33]:
filter_data

Peptide                                 R.[304.207]QQQHLFGSNVTD(C,57.021)SGNF(C,57.021)LFR.S  \
_dyn_#Symptomatic-non-COVID-19.JBDZ8                                             0.067680      
_dyn_#Symptomatic-non-COVID-19.JBDZ15                                            0.077130      
_dyn_#Healthy.HC27                                                               0.132415      
_dyn_#Non-severe-COVID-19.XG9                                                    0.063101      
_dyn_#Healthy.HC20                                                               0.074230      
...                                                                                   ...      
_dyn_#Non-severe-COVID-19.XG6                                                    0.048754      
_dyn_#Severe-COVID-19.XG43                                                       0.024494      
_dyn_#Symptomatic-non-COVID-19.JBDZ9                                             0.095905      
_dyn_#Symptomatic-non-COVID-19.JBDZ12                                            0.081779      
_dyn_#Severe-COVID-19.Patient-group-ZX                                           0.027799      

Peptide                                 R.[304.207]QQQHLF(G,304.219)SNVTD(C,57.021)SGNF(C,57.021)LFR.S  \
_dyn_#Symptomatic-non-COVID-19.JBDZ8                                             0.249860                
_dyn_#Symptomatic-non-COVID-19.JBDZ15                                            0.237354                
_dyn_#Healthy.HC27                                                               0.262200                
_dyn_#Non-severe-COVID-19.XG9                                                    0.194249                
_dyn_#Healthy.HC20                                                               0.388603                
...                                                                                   ...                
_dyn_#Non-severe-COVID-19.XG6                                                    0.528504                
_dyn_#Severe-COVID-19.XG43                                                       0.353784                
_dyn_#Symptomatic-non-COVID-19.JBDZ9                                             0.319936                
_dyn_#Symptomatic-non-COVID-19.JBDZ12                                            0.149601                
_dyn_#Severe-COVID-19.Patient-group-ZX                                           0.558448                

Peptide                                 K.[304.207]DLLFRDDTV(C,57.021)(L,134.957)A(K,304.207).L  \
_dyn_#Symptomatic-non-COVID-19.JBDZ8                                             0.257619         
_dyn_#Symptomatic-non-COVID-19.JBDZ15                                            0.979818         
_dyn_#Healthy.HC27                                                               1.051104         
_dyn_#Non-severe-COVID-19.XG9                                                    0.174534         
_dyn_#Healthy.HC20                                                               1.906894         
...                                                                                   ...         
_dyn_#Non-severe-COVID-19.XG6                                                    0.345443         
_dyn_#Severe-COVID-19.XG43                                                       0.697090         
_dyn_#Symptomatic-non-COVID-19.JBDZ9                                             0.271392         
_dyn_#Symptomatic-non-COVID-19.JBDZ12                                            0.123515         
_dyn_#Severe-COVID-19.Patient-group-ZX                                           0.142313         

Peptide                                 R.[304.207]DDTV(C,58.003)LA(K,304.207).L  \
_dyn_#Symptomatic-non-COVID-19.JBDZ8                                    0.145542   
_dyn_#Symptomatic-non-COVID-19.JBDZ15                                   0.168809   
_dyn_#Healthy.HC27                                                      0.361953   
_dyn_#Non-severe-COVID-19.XG9                    